# DIGI118 Oppgave 1d
---

**Lag først en kopi av denne notatboken ved hjelp av knappen øverst til høyre i dette vinduet. Nå er du klar til å kode i din egen versjon av denne notatboken.**

OBS: Når du forhåndsviser et diagram med `transform_filter`, må du kombinere det med det andre diagrammet som styrer filteret. Ellers vil det gi en feilmelding.

In [1]:
#########################################
# Data - Legg til ny kode og kopier over gammel kode fra tidligere notatbøker
#########################################

# Importer biblioteker, inkludert biblioteket som trengs for kartvisualisering
import pandas as pd
import altair as alt
import geopandas

# Lese inn sykkeldelingsdata og behandle dem etter behov
bike = pd.read_csv("bergen-bike-sharing-dataset-2023/bergen_sampled.csv")

# Les inn bergenskartdata og konverter denne topoJSON-filen til en dataramme for Altair
topo_src = "bydeler-bergen-map/bydeler-bergen.json"
bergen_topo = geopandas.read_file(topo_src, driver="TopoJSON")

# Preview dataframe
bike.head()

C:\Users\sebas\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\pyogrio\raw.py:198: RuntimeWarning: driver TopoJSON does not support open option DRIVER
  return ogr_read(


start_time             end_time  duration  start_station_id  \
0  2023-05-01 10:00:00  2023-05-01 10:00:00       384               639   
1  2023-05-01 11:00:00  2023-05-01 11:00:00       310                49   
2  2023-05-01 12:00:00  2023-05-01 12:00:00        99                 3   
3  2023-05-01 12:00:00  2023-05-01 13:00:00      4359               791   
4  2023-05-01 13:00:00  2023-05-01 13:00:00      1278               806   

       start_station_name  start_station_latitude  start_station_longitude  \
0         Frydenbø Marina               60.384467                 5.310008   
1     Studentsenteret UiB               60.387198                 5.322980   
2             Grieghallen               60.388197                 5.328564   
3      Busstasjonen 4 Sør               60.387059                 5.335634   
4  Dreggsallmenningen Sør               60.397709                 5.322001   

   end_station_id  end_station_name  end_station_latitude  \
0             819  Thormøhlens gate             60.383162   
1             151    Småstrandgaten             60.393098   
2             804         Stenersen             60.390174   
3             214     Nygårdsporten             60.383934   
4            2336     Møllestranden             60.380044   

   end_station_longitude  precipitation  temperature  wind_speed  weather  \
0               5.324053            0.0          6.7         5.3        3   
1               5.327023            0.0          7.8         5.6        3   
2               5.324792            0.0          8.2         7.5        3   
3               5.333450            0.0          8.2         7.5        3   
4               5.350824            0.0          8.1         8.2        4   

   sunshine  season  is_holiday  is_weekend  
0        60       0        True       False  
1        57       0        True       False  
2        25       0        True       False  
3        25       0        True       False  
4        38       0        True       False

In [2]:
#########################################
# Interaksjonsparametere - Kopier koden fra Oppgave 1c. Legg til ny kode for nye interaksjoner.
#########################################

#### Interaksjon ##########
# Angi et valg som lar brukeren velge et tidsintervall i tidsdiagrammet
brush_axis = alt.selection_interval(encodings=["x"])

# Skriv en betingelse som endrer fargen på datapunktene når de er valgt. Sett standardfargen til å være den ikke-valgte fargen.
color_brush = alt.condition(
    brush_axis,
    alt.value("#ef656b"),
    alt.value("#7572FF"),
    empty=False
)

In [3]:
#########################################
# Interaktivt tidsdiagram - Kopier kode over fra Oppgave 1c
#########################################

# Angi en tittel og beskrivelse for diagrammet.
chart_title = alt.TitleParams(
    "Bike usage over time",
    subtitle="Total number of bikes started each day",
    font="Helvetica", 
    fontWeight="bold",
    subtitleFont="Helvetica", 
    color="black",
    subtitleColor="black",
    subtitleFontStyle="italic",
    fontSize=20,
    subtitleFontSize=12,
    anchor="start", # specifies position for placing the title (middle by default, or start, end)
    orient="top", # specifies title orientation around chart (top by default, or bottom, left, right)
    offset=20 #space in pixels between title and chart  
)

# Tegn et histogram med en diagramtittel og interaksjon.
bike_chart = alt.Chart(bike, title=chart_title).mark_bar(color="#7572FF").encode(
    alt.X('yearmonthdate(start_time):T', title="Start Time"),
    alt.Y('count():Q', title="Total Rides"),
    color = color_brush,
    tooltip=[alt.Tooltip('start_time:T', title="Date"), alt.Tooltip('count():Q', title="Total Rides")]
).add_params(
    brush_axis
).properties(
    width=550,
    height=100
)

bike_chart

alt.Chart(...)

In [4]:
#########################################
# Punktplott (knyttet til tidsdiagram) - Kopier koden fra Oppgave 1c. Legg til ny kode for interaksjoner etter behov.
#########################################

# Angi en diagramtittel og beskrivelse.
chart_title = alt.TitleParams(
    "Total bike rides started and ended at each station",
    subtitle="Open [red] circles are starting stations, filled [blue] circles are ending stations",
    font="Helvetica", 
    fontWeight="bold",
    subtitleFont="Helvetica", 
    color="Black",
    subtitleColor="black",
    subtitleFontStyle="italic",
    fontSize=20,
    subtitleFontSize=12,
    anchor="start", # specifies position for placing the title (middle by default, or start, end)
    offset=25 #space in pixels between title and chart  
)

#### Tegn et lagdelt prikkplott for de totale turene som starter og slutter ved hver stasjon.####

# Tegn først de individuelle prikkplottene
bike_start = alt.Chart(bike).mark_point(color="#ef656b").encode(
    alt.X('count():Q', title="Total Rides"),
    alt.Y('start_station_name:N', title=None).sort("-x"),
    tooltip=[alt.Tooltip("start_station_name:N", title="Station Name (Started)"), alt.Tooltip('count():Q', title="Total Rides")]
)


bike_end = alt.Chart(bike).mark_circle(color="#7572FF").encode(
    alt.X('count():Q', title="Total Rides"),
    alt.Y('end_station_name:N', title=None).sort("-x"),
    tooltip=[alt.Tooltip("end_station_name:N", title="Station Name (Ended)"), alt.Tooltip('count():Q', title="Total Rides")]
)

# Legg de individuelle diagrammene i lag.
layered_bike = (bike_start + bike_end).properties(
    title=chart_title,
    width=300,
    height=1000
).transform_filter(
    brush_axis
)

bike_chart | layered_bike

alt.HConcatChart(...)

In [11]:
#########################################
# Levert kode: Hjelpefunksjoner for kart
#########################################

# Undertrykk ShapelyDeprecationWarning for rideify
import warnings
from shapely.errors import ShapelyDeprecationWarning
warnings.filterwarnings("ignore", category=ShapelyDeprecationWarning)

# Importer biblioteker som kreves for rideify
import numpy as np
from shapely.geometry import LineString

# Rideify
def rideify(df):
    """
    Helper function to create a geoshape LineString object that draws as-the-crow-flies 
    from start coord to end coord 

    Result of row-wise function must be converted back to a GeoSeries to be used in plotting
    """
    rides = df.apply(
        lambda d:LineString(
            np.array([
                (d["start_station_longitude"], d["start_station_latitude"]),
                (d["end_station_longitude"], d["end_station_latitude"])
            ]),
        ),
        axis=1
    )

    return geopandas.GeoSeries(rides)

# Zoomify
def zoomify(df_topojson, bydel_focus, adj_xmin, adj_ymin, adj_xmax, adj_ymax):
    """
    Control zoom to a portion of a geojson file 
    Source map is df_topojson 
    Focus area is bydel_focus, e.g., "Bergenhus"
    adj_XXX variables allow to shift frame in 
    x_min (left border), 
    x_max (right border), 
    y_min (bottom border), 
    y_max (top border)

    fit object is output as a GeoJSON-like Feature or FeatureCollection 
    that can be used in .project() for alt.Chart()
    """
    extent_roi = df_topojson.query(f"bydelnavn == '{bydel_focus}'")
    xmin, ymin, xmax, ymax = extent_roi.total_bounds

    # fit object should be a GeoJSON-like Feature or FeatureCollection
    extent_roi_feature = {
        "type": "Feature",
        "geometry": {"type": "Polygon",
                    "coordinates": [[
                        [xmax + adj_xmax, ymax + adj_ymax],  # top right
                        [xmax + adj_xmax, ymin + adj_ymin],  # bottom right

                        [xmin + adj_xmin, ymin + adj_ymin],  # bottom left 
                        [xmin + adj_xmin, ymax + adj_ymax],  # top left
                        [xmax + adj_xmax, ymax + adj_ymax],   # top right again
                        ]]
                    },
        "properties": {}
    }
    return extent_roi_feature

In [6]:
#########################################
# Kart: Base - ny kode
#########################################

# Tegn et basislag for kartoversikten
bergen_map = alt.Chart(bergen_topo).mark_geoshape(
    clip=True
).encode(
    stroke= alt.Stroke("bydelnavn:N", legend=alt.Legend(
        orient='left')),
    fill=alt.value("whitesmoke")
).project(
    fit=zoomify(
        bergen_topo, # map dataframe
        "Bergenhus", # district to focus on
        0.05,    # adjust xmin
        -0.035,    # adjust ymin  
        -0.08,    # adjust xmax 
        -0.01     # adjust ymax
        ),
)
bergen_map


alt.Chart(...)

In [7]:
#########################################
# Kart: Datapunkter - ny kode
#########################################

# Tegn et datapunktlag for kartdiagrammet som viser plasseringen av sykkelstasjoner i Bergen.
bike_points = alt.Chart(bike).mark_circle(
    stroke="#174abf",
    strokeWidth= 1,
).encode(
    longitude="start_station_longitude:Q",
    latitude="start_station_latitude:Q",
    color=alt.value("#7572FF"),
    opacity=alt.value(0.9),
    size=alt.Size("count():Q", title="Total rides", legend=alt.Legend(
        orient='left')),
    tooltip=[alt.Tooltip("start_station_name:N", title="Station Name (Started)"), alt.Tooltip('count():Q', title="Total Rides")]
).transform_filter(
    brush_axis
)

# Valgfritt: Tegn "as the crow flies" mellom stasjonene ved hjelp av hjelpefunksjonen rideify()
bikes = pd.read_csv("bergen-bike-sharing-dataset-2023/bergen_sampled.csv")

paths = alt.Chart(
    rideify(bikes)
).mark_geoshape(
    filled = False,
    opacity = 0.1,
    color = "#b5caf2",
)



In [8]:
#########################################
# Kart: Endelig lagdelt kart - ny kode
#########################################

# Angi karttittel og beskrivelse for kartdiagrammet
map_title = alt.TitleParams(
    "Bike sharing in Bergen",
    subtitle="Bike stations are available, and broadly used, across the city parts",
    font="Helvetica", 
    fontWeight="bold",
    subtitleFont="Helvetica", 
    color="Black",
    subtitleColor="black",
    subtitleFontStyle="italic",
    fontSize=20,
    subtitleFontSize=12,
    anchor="start", # specifies position for placing the title (middle by default, or start, end)
    offset=25 #space in pixels between title and chart  
)

# Tegn det endelige kartkartet som lagdeler basen og datapunktene (valgfritt: og "as the crow flies").
# Husk å angi en kartprojeksjon. Valgfritt: Du kan bruke hjelpefunksjonen zoomify() for å zoome inn kartet til Bergenhus.

bergen_bike_map = (bergen_map + paths + bike_points)


In [12]:
#########################################
# Kombiner diagrammer til et dashbord - ny kode
#########################################

# Angi dashbordets tittel og beskrivelse.
dashb_title = alt.TitleParams(
        "Bike sharing in Bergen",
        subtitle="Bike stations are available, and broadly used, across the city parts",
        fontSize = 20,
        anchor='middle',
        offset=20,
   )

# Kombiner de tre diagrammene til et dashbord (og test interaksjonene for å sikre at de fungerer).
# Husk at du kan legge til konfigurasjoner på toppnivå her, f.eks. tegnforklaring, tittel, akse
bergen_bike_dashboard = (bergen_bike_map & bike_chart | layered_bike
).properties(
    title=dashb_title,
).configure_title( #Applied to all "title=" specifications
    font="Futura",
    color="Grey"
)

# Vis den endelige visualiseringen av dashbordet
bergen_bike_dashboard

alt.HConcatChart(...)

In [10]:
# Lagre dashbordet i Kaggles Output-arbeidsmappe for å kunne laste det ned.
(bergen_bike_dashboard).save("Bergen_bike_chart.html")

---

### OBS: Send inn denne endelige notatboken til oss.
Koden du har skrevet her vil være den endelige notatboken som inneholder all koden du har skrevet for å lage den endelige dashbordvisualiseringen for dette kurset. Last ned denne notatboken (File > Download Notebook), eksporter en visualiseringsfil (HTML) fra koden din, og send begge disse filene til MittUiB.

# Ressurser
### Kaggle Notebooks
- [DIGI118 Modul 0: Heisann, Python!](https://www.kaggle.com/code/lauragarrison/digi118-h24-modul-0-heisann-python) 
- [DIGI118 Modul 0: Heisann, Pandas!](https://www.kaggle.com/code/lauragarrison/digi118-h24-modul-0-heisann-pandas)
- [DIGI118 Modul 1: Heisann, Altair!](https://www.kaggle.com/code/lauragarrison/digi118-modul-1-heisann-altair)
- [DIGI118 Modul 2: Det riktige diagrammet for jobben](https://www.kaggle.com/code/amykzhang/digi118-modul-2-det-riktige-diagrammet-for-jobben) 
- [DIGI118 Modul 3: Gjør det interaktivt](https://www.kaggle.com/code/amykzhang/digi118-modul-3-gj-r-det-interaktivt)
- [DIGI118 Modul 4: Kart og mer](https://www.kaggle.com/code/amykzhang/digi118-modul-4-kart-og-mer)

### Dokumentasjon
- Pandas-dokumentasjon: https://pandas.pydata.org/docs/reference/index.html
- Altair-dokumentasjon: https://altair-viz.github.io/user_guide/api.html
- Altair User Guide to Customization: https://altair-viz.github.io/user_guide/customization.html
- Altair User Guide to Interaction: https://altair-viz.github.io/user_guide/interactions.html
- Altair User Guide to GeoShapes: https://altair-viz.github.io/user_guide/marks/geoshape.html
- Altair User Guide to Top-Level Chart Configurations: https://altair-viz.github.io/user_guide/configuration.html
- Eksempler på Altair-diagrammer, inkludert histogrammer: https://altair-viz.github.io/gallery